In [27]:
import utils as utils
import numpy as np
import karoke
import librosa

from pprint import pprint
from random import sample
from importlib import reload

from lyrics import lyrics
from audio import download_audio

In [14]:
%%script false --no-raise-error
info = download_audio("https://www.youtube.com/watch?v=asew9BF1wdw")

In [15]:
sr, x = utils.read("Sabrina Carpenter - Feather (Lyric Video).wav")
time_lines = lyrics("2Zo1PcszsT9WQ0ANntJbID")  # [(ms, lyric)]
times = np.array([t for t, _ in time_lines])  # [ms]
lines = np.array([l for _, l in time_lines])  # [lyric]

# TODO: Filter out chorus by dropping {"(", ")"}?

x = x.T[0] + x.T[1]  # Mono-ify


def ms_to_sample(ms: int, sr: int) -> int:
    return int(ms * sr / 1000)

In [16]:
samples_i = np.random.choice(len(time_lines) - 3, 5)  # i, i + 1, i + 2
samples_block = np.stack(
    (lines[samples_i], lines[samples_i + 1], lines[samples_i + 2])
).T

for i, (l, c, r) in zip(samples_i, samples_block):
    utils.sound(
        x[ms_to_sample(times[i], sr) : ms_to_sample(times[i + 3], sr)],
        sr,
        "\n".join((l, c, r)),
    )

In [35]:
reload(karoke)

i, (l, c, r) = samples_i[0], samples_block[0]

x = x.astype(np.float32)

removed = karoke.remove_vocals(
    x[ms_to_sample(times[i + 1], sr) : ms_to_sample(times[i + 2], sr)]
)

loading model... done
(2, 192000)
stft of input x... done


100%|██████████| 1/1 [00:07<00:00,  7.57s/it]

validating output directory... done
inverse stft of instruments... done


In [37]:
print(removed.shape)

utils.sound(removed, sr)

utils.sound(
    np.concatenate(
        (
            x[ms_to_sample(times[i], sr) : ms_to_sample(times[i + 1], sr)],
            removed,
            x[ms_to_sample(times[i + 2], sr) : ms_to_sample(times[i + 3], sr)],
        )
    ),
    sr,
    "\n".join((l, c, r)),
)

(191488,)
